In [1]:
from safetensors import safe_open

lora = {}
with safe_open("/data2/bjh/diffusion-pipe/cosmos_test/20250327_02-37-25/epoch5/adapter_model.safetensors", framework="pt", device='cpu') as f:
    for k in f.keys():
        lora[k] = f.get_tensor(k)

In [2]:
tensors = {}
with safe_open("/data2/bjh/ComfyUI/models/diffusion_models/Cosmos-1_0-Diffusion-14B-Text2World.safetensors", framework="pt", device='cpu') as f:
    for k in f.keys():
        tensors[k] = f.get_tensor(k)

In [3]:
len(lora)

1152

In [4]:
name_lis = []
for k in lora:
    a = k.split('.')[1:][:-2]
    name = '.'.join(a)
    name_lis.append(name)
name_lis=set(name_lis)

In [5]:
import torch
new_dic = {}
for k in tensors:
    name='.'.join(k.split('.')[1:][:-1])
    if name in name_lis:
        a,b = lora['diffusion_model.'+name+'.lora_A.weight'],lora['diffusion_model.'+name+'.lora_B.weight']
        new_dic[k]=tensors[k]+torch.matmul(b,a)
    else:
        new_dic[k]=tensors[k]

In [6]:
from safetensors.torch import save_file
save_file(new_dic,'test.safetensors')